<h1 id="tocheading">Table of Contents</h1>
<div id="toc"></div>

In [1]:
!pip install xlrd
!pip install geocoder
!pip install holidays-es

In [2]:
%%javascript
$.getScript('https://kmahelona.github.io/ipython_notebook_goodies/ipython_notebook_toc.js')

<IPython.core.display.Javascript object>

# Setting up the Jupyter Notebook

All imports and configutations to set up the model are done here.

In [3]:
from IPython.core.display import display, HTML

display(HTML("<style>.container { width:100% !important; }</style>")) # Increase cell width
display(HTML("<style>.rendered_html { font-size: 16px; }</style>")) # Increase font size


# for data manipulation
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import xlrd
pd.set_option('display.max_columns', 60)
import json
import geocoder
from holidays_es import Province

# for visualization
from IPython.core.pylabtools import figsize
from matplotlib import pyplot as plt
%matplotlib inline
# to include graphs inline within the frontends next to code
import seaborn as sns
sns.set_context(font_scale=2)
import folium

# to bypass warnings in various dataframe assignments
pd.options.mode.chained_assignment = None

# machine learning models
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from xgboost import XGBClassifier
from sklearn.linear_model import LogisticRegression

# preprocessing functions and evaluation models
from sklearn.model_selection import train_test_split, RandomizedSearchCV, GridSearchCV
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.dummy import DummyClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import GradientBoostingClassifier

/var/folders/t6/zsjg3m1n24j8rfy40ynr1r4w0000gn/T/ipykernel_56485/3645222141.py:1: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


# 1. Understand, Clean and Format Data

To understand how data is structured, I am going to look at:
* First and last rows
* Information
* Descriptive statistics of the dataset.

and apply cleaning and formatting afterwards, if necessary.

## Data Loading

In [4]:
_df_clima = pd.read_csv("CLIMA.csv")
_df_ventas = pd.read_csv("VENTAS.csv")
_df_ventas = _df_ventas.apply(pd.to_numeric, errors='coerce')
_df_ventas_part1 = pd.read_csv("VENTAS_PART1.csv")
_df_ventas_part1 = _df_ventas_part1.apply(pd.to_numeric, errors='coerce')
_df_ventas_part2 = pd.read_csv("VENTAS_PART2.csv")
_df_ventas_part2 = _df_ventas_part2.apply(pd.to_numeric, errors='coerce')
_df_promociones = pd.read_csv("PROMOCIONES.csv")
df = _df_ventas.apply(pd.to_numeric, errors='coerce')
_df_proyecciones = pd.read_csv("PROYECCIONES.csv")
df = _df_ventas.apply(pd.to_numeric, errors='coerce')
_df_diccionario=pd.read_excel("DICCIONARIO.xlsx",sheet_name=None)
_df_proyecciones_xlsx=pd.read_excel("PROYECCIONES.xlsx")

#print("Number of rows and columns in train data set are:",train_initial.shape)
#train_initial.head()
#test_initial.head()
#print("Number of rows and columns in test data set are:",test_initial.shape)

In [36]:
_df_Censo_xlsx=pd.read_excel("Censo.xlsx")
_df_Censo_xlsx

Provincia.year       Men     women
0                        Albacete.2022  165076.0  171002.0
1                        Albacete.2021  165049.0  170781.0
2                        Albacete.2020  165078.0  171138.0
3                        Albacete.2019  164388.0  170596.0
4                        Albacete.2018  164303.0  170178.0
..                                 ...       ...       ...
259                       Melilla.2018   30717.0   31217.0
260                                NaN       NaN       NaN
261                                NaN       NaN       NaN
262                           Fuente:        NaN       NaN
263  Instituto Nacional de Estadística       NaN       NaN

[264 rows x 3 columns]

In [5]:
_df_diccionario['Products']

cod_producto CATEGORY       SEGMENT         MANUFACTURER  \
0                1     BEER      ARTISANS  OTHER MANUFACTURERS   
1                2     BEER      ARTISANS  OTHER MANUFACTURERS   
2                3     BEER      ARTISANS  OTHER MANUFACTURERS   
3                4     BEER      ARTISANS  OTHER MANUFACTURERS   
4                5     BEER      ARTISANS  OTHER MANUFACTURERS   
...            ...      ...           ...                  ...   
1503          1504     BEER  ZERO ALCOHOL       MANUFACTURER 3   
1504          1505     BEER  ZERO ALCOHOL       MANUFACTURER 1   
1505          1506     BEER  ZERO ALCOHOL  OTHER MANUFACTURERS   
1506          1507     BEER  ZERO ALCOHOL       MANUFACTURER 1   
1507          1508     BEER  ZERO ALCOHOL  OTHER MANUFACTURERS   

                         BRAND       PACKAGING  \
0     OTHER MAN - OTHER BRANDS  CRISTAL BOTTLE   
1     OTHER MAN - OTHER BRANDS  CRISTAL BOTTLE   
2     OTHER MAN - OTHER BRANDS  CRISTAL BOTTLE   
3     OTHER MAN - OTHER BRANDS  CRISTAL BOTTLE   
4     OTHER MAN - OTHER BRANDS  CRISTAL BOTTLE   
...                        ...             ...   
1503           MAN 3 - BRAND 4             CAN   
1504      MAN 1 - OTHER BRANDS             CAN   
1505  OTHER MAN - OTHER BRANDS  CRISTAL BOTTLE   
1506      MAN 1 - OTHER BRANDS             CAN   
1507  OTHER MAN - OTHER BRANDS             CAN   

                                   VOLUME                                UNITS  
0     330ML                                1CT                                  
1     330ML                                1CT                                  
2     330ML                                1CT                                  
3     330ML                                1CT                                  
4     330ML                                1CT                                  
...                                   ...                                  ...  
1503  330ML                                1CT                                  
1504  330ML                                1CT                                  
1505  330ML                                6CT                                  
1506  330ML                                1CT                                  
1507  330ML                                1CT                                  

[1508 rows x 8 columns]

In [6]:
display(_df_ventas.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5730092 entries, 0 to 5730091
Data columns (total 11 columns):
 #   Column                  Dtype  
---  ------                  -----  
 0   cod_tienda              int64  
 1   cod_semana              int64  
 2   cod_producto            int64  
 3   ventas_unidades         int64  
 4   ventas_valor            float64
 5   ventas_volumen          int64  
 6   numero_referencias      int64  
 7   precio_real_unidades    float64
 8   precio_real_volumen     float64
 9   precio_tarifa_unidades  float64
 10  precio_tarifa_volumen   float64
dtypes: float64(5), int64(6)
memory usage: 480.9 MB


None

In [7]:
display(_df_ventas.describe())

cod_tienda    cod_semana  cod_producto  ventas_unidades  \
count  5.730092e+06  5.730092e+06  5.730092e+06     5.730092e+06   
mean   2.754999e+02  6.644391e+01  8.711387e+02     4.880012e+01   
std    1.620264e+02  3.812740e+01  4.079503e+02     5.120601e+02   
min    1.000000e+00  1.000000e+00  4.000000e+00     0.000000e+00   
25%    1.480000e+02  3.400000e+01  5.160000e+02     3.000000e+00   
50%    2.640000e+02  6.600000e+01  9.270000e+02     9.000000e+00   
75%    4.220000e+02  9.800000e+01  1.229000e+03     2.700000e+01   
max    5.570000e+02  1.400000e+02  1.506000e+03     1.748640e+05   

       ventas_valor  ventas_volumen  numero_referencias  precio_real_unidades  \
count  5.730092e+06    5.730092e+06           5730092.0          5.730092e+06   
mean   4.781000e+01    3.715636e+01                 1.0          2.153014e+00   
std    2.293336e+02    2.495483e+02                 0.0          2.425966e+00   
min    2.000000e-02    0.000000e+00                 1.0          1.000000e-02   
25%    5.160000e+00    2.000000e+00                 1.0          6.200000e-01   
50%    1.272000e+01    6.000000e+00                 1.0          1.210000e+00   
75%    3.268000e+01    2.000000e+01                 1.0          2.630000e+00   
max    6.803865e+04    5.770500e+04                 1.0          1.390000e+02   

       precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  
count         5.730092e+06            5.730092e+06           5.730092e+06  
mean          1.164593e+00            2.257827e+00           1.164593e+00  
std           1.526817e+00            2.624847e+00           1.526817e+00  
min           2.000000e-01            1.000000e-02           2.000000e-01  
25%           3.300000e-01            6.500000e-01           3.300000e-01  
50%           3.600000e-01            1.280000e+00           3.600000e-01  
75%           1.500000e+00            2.660000e+00           1.500000e+00  
max           5.000000e+01            1.408500e+02           5.000000e+01

In [8]:
from pandas_profiling import ProfileReport
report = ProfileReport(_df_ventas, minimal=False)
report

/Users/proddo/opt/anaconda3/lib/python3.9/site-packages/llvmlite/llvmpy/__init__.py:3: UserWarning: The module `llvmlite.llvmpy` is deprecated and will be removed in the future.
  warnings.warn(
/Users/proddo/opt/anaconda3/lib/python3.9/site-packages/llvmlite/llvmpy/core.py:8: UserWarning: The module `llvmlite.llvmpy.core` is deprecated and will be removed in the future. Equivalent functionality is provided by `llvmlite.ir`.
  warnings.warn(
/Users/proddo/opt/anaconda3/lib/python3.9/site-packages/llvmlite/llvmpy/passes.py:17: UserWarning: The module `llvmlite.llvmpy.passes` is deprecated and will be removed in the future. If you are using this code, it should be inlined into your own project.
  warnings.warn(


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
_df_ventas.head()

cod_tienda  cod_semana  cod_producto  ventas_unidades  ventas_valor  \
0         243          42           236               30         19.50   
1         243          42           239                2          1.82   
2         243          42           247                2         10.32   
3         243          42           258                3         14.97   
4         243          42           264                2         10.88   

   ventas_volumen  numero_referencias  precio_real_unidades  \
0              10                   1                  0.65   
1               1                   1                  0.91   
2               4                   1                  5.16   
3               6                   1                  4.99   
4               4                   1                  5.44   

   precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  
0                 0.33                    0.65                   0.33  
1                 0.33                    0.91                   0.33  
2                 1.98                    5.16                   1.98  
3                 1.98                    4.99                   1.98  
4                 1.98                    5.44                   1.98

In [10]:
_df_ventas_part2.head()

cod_tienda  cod_semana  cod_producto  ventas_unidades  ventas_valor  \
0         485          34          1378               12         12.00   
1         485          34          1379                3          7.05   
2         485          34          1380               18          9.18   
3         485          34          1382                6          2.64   
4         485          34          1384                4          7.40   

   ventas_volumen  numero_referencias  precio_real_unidades  \
0              12                   1                  1.00   
1               5                   1                  2.35   
2               6                   1                  0.51   
3               2                   1                  0.44   
4               6                   1                  1.85   

   precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  
0                 1.00                    1.23                   1.00  
1                 1.50                    2.35                   1.50  
2                 0.33                    0.51                   0.33  
3                 0.33                    0.56                   0.33  
4                 1.50                    1.85                   1.50

In [11]:
display(_df_ventas.describe())

cod_tienda    cod_semana  cod_producto  ventas_unidades  \
count  5.730092e+06  5.730092e+06  5.730092e+06     5.730092e+06   
mean   2.754999e+02  6.644391e+01  8.711387e+02     4.880012e+01   
std    1.620264e+02  3.812740e+01  4.079503e+02     5.120601e+02   
min    1.000000e+00  1.000000e+00  4.000000e+00     0.000000e+00   
25%    1.480000e+02  3.400000e+01  5.160000e+02     3.000000e+00   
50%    2.640000e+02  6.600000e+01  9.270000e+02     9.000000e+00   
75%    4.220000e+02  9.800000e+01  1.229000e+03     2.700000e+01   
max    5.570000e+02  1.400000e+02  1.506000e+03     1.748640e+05   

       ventas_valor  ventas_volumen  numero_referencias  precio_real_unidades  \
count  5.730092e+06    5.730092e+06           5730092.0          5.730092e+06   
mean   4.781000e+01    3.715636e+01                 1.0          2.153014e+00   
std    2.293336e+02    2.495483e+02                 0.0          2.425966e+00   
min    2.000000e-02    0.000000e+00                 1.0          1.000000e-02   
25%    5.160000e+00    2.000000e+00                 1.0          6.200000e-01   
50%    1.272000e+01    6.000000e+00                 1.0          1.210000e+00   
75%    3.268000e+01    2.000000e+01                 1.0          2.630000e+00   
max    6.803865e+04    5.770500e+04                 1.0          1.390000e+02   

       precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  
count         5.730092e+06            5.730092e+06           5.730092e+06  
mean          1.164593e+00            2.257827e+00           1.164593e+00  
std           1.526817e+00            2.624847e+00           1.526817e+00  
min           2.000000e-01            1.000000e-02           2.000000e-01  
25%           3.300000e-01            6.500000e-01           3.300000e-01  
50%           3.600000e-01            1.280000e+00           3.600000e-01  
75%           1.500000e+00            2.660000e+00           1.500000e+00  
max           5.000000e+01            1.408500e+02           5.000000e+01

In [12]:
_df_ventas.isnull().values.any()

False

In [13]:
(_df_ventas < 0).values.any()

False

In [14]:
_df_ventas.describe()

cod_tienda    cod_semana  cod_producto  ventas_unidades  \
count  5.730092e+06  5.730092e+06  5.730092e+06     5.730092e+06   
mean   2.754999e+02  6.644391e+01  8.711387e+02     4.880012e+01   
std    1.620264e+02  3.812740e+01  4.079503e+02     5.120601e+02   
min    1.000000e+00  1.000000e+00  4.000000e+00     0.000000e+00   
25%    1.480000e+02  3.400000e+01  5.160000e+02     3.000000e+00   
50%    2.640000e+02  6.600000e+01  9.270000e+02     9.000000e+00   
75%    4.220000e+02  9.800000e+01  1.229000e+03     2.700000e+01   
max    5.570000e+02  1.400000e+02  1.506000e+03     1.748640e+05   

       ventas_valor  ventas_volumen  numero_referencias  precio_real_unidades  \
count  5.730092e+06    5.730092e+06           5730092.0          5.730092e+06   
mean   4.781000e+01    3.715636e+01                 1.0          2.153014e+00   
std    2.293336e+02    2.495483e+02                 0.0          2.425966e+00   
min    2.000000e-02    0.000000e+00                 1.0          1.000000e-02   
25%    5.160000e+00    2.000000e+00                 1.0          6.200000e-01   
50%    1.272000e+01    6.000000e+00                 1.0          1.210000e+00   
75%    3.268000e+01    2.000000e+01                 1.0          2.630000e+00   
max    6.803865e+04    5.770500e+04                 1.0          1.390000e+02   

       precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  
count         5.730092e+06            5.730092e+06           5.730092e+06  
mean          1.164593e+00            2.257827e+00           1.164593e+00  
std           1.526817e+00            2.624847e+00           1.526817e+00  
min           2.000000e-01            1.000000e-02           2.000000e-01  
25%           3.300000e-01            6.500000e-01           3.300000e-01  
50%           3.600000e-01            1.280000e+00           3.600000e-01  
75%           1.500000e+00            2.660000e+00           1.500000e+00  
max           5.000000e+01            1.408500e+02           5.000000e+01

In [15]:
_df_ventas.cod_semana.unique()

array([ 42,  22, 130, 139,  88,  83,  96, 103,  17, 129, 113,  33,  37,
       105, 108,  44,  64,  62,  24, 104, 115,  68,   9,  27, 121, 126,
       111, 138, 136,  92, 100, 106,  36,  53,  28,  21,  89,  66,  14,
        11,  23,  40,  94,  84, 101,  19,  48,  49, 117,  69, 122, 137,
        15,  20, 132,  78,  91,  76, 119,  75,  25,  43,  58,  77, 131,
        51,  39,  99,  90, 116,  31,  30,   5,  93, 112,  52,  72,  45,
       123,  61, 110, 102, 133, 134,  12,  70,  87,  13,  10,  97, 135,
        95,  57, 120,  82, 128,  32,   8,  26,   1,  74,  79, 114, 109,
        16,   2,  56,   7,  63,  18,  67,  46,  47,   6,   4, 125,  50,
        98, 127,  34,  35,  73, 140,  55, 118,  71,  41,  59,  80,  85,
         3, 124,  29,  60, 107,  38,  54,  81,  86,  65])

In [16]:
_df_ventas[_df_ventas.cod_semana > 116].cod_semana.unique()

array([130, 139, 129, 121, 126, 138, 136, 117, 122, 137, 132, 119, 131,
       123, 133, 134, 135, 120, 128, 125, 127, 140, 118, 124])

In [17]:
_df_proyecciones = pd.read_csv("PROYECCIONES.csv",sep=';')

In [18]:
_df_proyecciones.describe()

cod_tienda    cod_semana
count  43984.000000  43984.000000
mean     283.274600     58.575550
std      162.127945     33.471862
min        1.000000      1.000000
25%      146.000000     30.000000
50%      280.000000     59.000000
75%      430.000000     88.000000
max      557.000000    116.000000

In [19]:
def week_to_month_year_season(week_code,year):
    year, week_num, day_of_week = datetime.date.fromisocalendar(year, week_code, week_start=7).isocalendar()
    month = datetime.date(year, 1, 1).replace(day=1).replace(month=1).replace(day=(((week_num-1)*7)+1)).strftime('%B')
    if month in ['March', 'April', 'May']:
        season = 'Spring'
    elif month in ['June', 'July', 'August']:
        season = 'Summer'
    elif month in ['September', 'October', 'November']:
        season = 'Fall'
    else:
        season = 'Winter'
    return month, year, season

In [20]:
from datetime import datetime, timedelta

def week_to_month_year_season(week_code, year):
    start_date = datetime(year, 1, 1)
    week_start = 6  # Sunday
    week_end = 5  # Saturday
    week_delta = timedelta(days=7)

    # Calculate the start and end dates of the given week code
    start_of_week = start_date + timedelta(days=(week_code - 1) * 7 - start_date.weekday() + week_start)
    end_of_week = start_of_week + week_delta - timedelta(days=1)

    # Extract the month, year, and season from the start of the week
    month = start_of_week.strftime('%B')
    year = start_of_week.year

    if month in ['March', 'April', 'May']:
        season = 'Spring'
    elif month in ['June', 'July', 'August']:
        season = 'Summer'
    elif month in ['September', 'October', 'November']:
        season = 'Fall'
    else:
        season = 'Winter'

    return month, year, season


In [21]:
_df_ventas[['month', 'year', 'season']] = df.apply(lambda row: pd.Series(week_to_month_year_season(row['cod_semana'], 2021)), axis=1)

In [42]:
_df_Stores=_df_diccionario['Stores']
_df_Provinces=_df_diccionario['Provinces']
_df_Products=_df_diccionario['Products']

In [24]:
_df_ventas=_df_ventas.merge(_df_Stores, on='cod_tienda', how='left')


In [25]:
_df_ventas=_df_ventas.merge(_df_Products, on='cod_producto', how='left')
_df_ventas

cod_tienda  cod_semana  cod_producto  ventas_unidades  ventas_valor  \
0               243          42           236               30         19.50   
1               243          42           239                2          1.82   
2               243          42           247                2         10.32   
3               243          42           258                3         14.97   
4               243          42           264                2         10.88   
...             ...         ...           ...              ...           ...   
5730087         526          47           625              100        127.00   
5730088         526          47           633               20         49.00   
5730089         526          47           652                6         37.50   
5730090         526          47           654               23         85.10   
5730091         526          47           655               46         55.20   

         ventas_volumen  numero_referencias  precio_real_unidades  \
0                    10                   1                  0.65   
1                     1                   1                  0.91   
2                     4                   1                  5.16   
3                     6                   1                  4.99   
4                     4                   1                  5.44   
...                 ...                 ...                   ...   
5730087              36                   1                  1.27   
5730088              10                   1                  2.45   
5730089              18                   1                  6.25   
5730090              35                   1                  3.70   
5730091              15                   1                  1.20   

         precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  \
0                       0.33                    0.65                   0.33   
1                       0.33                    0.91                   0.33   
2                       1.98                    5.16                   1.98   
3                       1.98                    4.99                   1.98   
4                       1.98                    5.44                   1.98   
...                      ...                     ...                    ...   
5730087                 0.36                    1.27                   0.36   
5730088                 0.50                    2.45                   0.50   
5730089                 3.00                    6.25                   3.00   
5730090                 1.50                    3.70                   1.50   
5730091                 0.33                    1.20                   0.33   

            month  year season  cod_canal  cod_provincia  postal_code  \
0         October  2021   Fall          1             26        26003   
1         October  2021   Fall          1             26        26003   
2         October  2021   Fall          1             26        26003   
3         October  2021   Fall          1             26        26003   
4         October  2021   Fall          1             26        26003   
...           ...   ...    ...        ...            ...          ...   
5730087  November  2021   Fall          2             91         8029   
5730088  November  2021   Fall          2             91         8029   
5730089  November  2021   Fall          2             91         8029   
5730090  November  2021   Fall          2             91         8029   
5730091  November  2021   Fall          2             91         8029   

         sales_surface_sqmeters CATEGORY         SEGMENT         MANUFACTURER  \
0                          1500     BEER           EXTRA       MANUFACTURER 2   
1                          1500     BEER           EXTRA       MANUFACTURER 2   
2                          1500     BEER           EXTRA       MANUFACTURER 2   
3                          1500     BEER           EXTRA       MANUFA

In [37]:
_df_ventas=_df_ventas.merge(_df_Provinces_enriched_x_y, on='cod_provincia', how='left')

In [38]:
_df_ventas_historic=_df_ventas[_df_ventas.cod_semana <= 116]

In [39]:
_df_ventas_projected=_df_ventas[_df_ventas.cod_semana > 116]

In [40]:
_df_ventas_historic

cod_tienda  cod_semana  cod_producto  ventas_unidades  ventas_valor  \
0               243          42           236               30         19.50   
1               243          42           239                2          1.82   
2               243          42           247                2         10.32   
3               243          42           258                3         14.97   
4               243          42           264                2         10.88   
...             ...         ...           ...              ...           ...   
5730087         526          47           625              100        127.00   
5730088         526          47           633               20         49.00   
5730089         526          47           652                6         37.50   
5730090         526          47           654               23         85.10   
5730091         526          47           655               46         55.20   

         ventas_volumen  numero_referencias  precio_real_unidades  \
0                    10                   1                  0.65   
1                     1                   1                  0.91   
2                     4                   1                  5.16   
3                     6                   1                  4.99   
4                     4                   1                  5.44   
...                 ...                 ...                   ...   
5730087              36                   1                  1.27   
5730088              10                   1                  2.45   
5730089              18                   1                  6.25   
5730090              35                   1                  3.70   
5730091              15                   1                  1.20   

         precio_real_volumen  precio_tarifa_unidades  precio_tarifa_volumen  \
0                       0.33                    0.65                   0.33   
1                       0.33                    0.91                   0.33   
2                       1.98                    5.16                   1.98   
3                       1.98                    4.99                   1.98   
4                       1.98                    5.44                   1.98   
...                      ...                     ...                    ...   
5730087                 0.36                    1.27                   0.36   
5730088                 0.50                    2.45                   0.50   
5730089                 3.00                    6.25                   3.00   
5730090                 1.50                    3.70                   1.50   
5730091                 0.33                    1.20                   0.33   

            month  year season  cod_canal  cod_provincia  postal_code  \
0         October  2021   Fall          1             26        26003   
1         October  2021   Fall          1             26        26003   
2         October  2021   Fall          1             26        26003   
3         October  2021   Fall          1             26        26003   
4         October  2021   Fall          1             26        26003   
...           ...   ...    ...        ...            ...          ...   
5730087  November  2021   Fall          2             91         8029   
5730088  November  2021   Fall          2             91         8029   
5730089  November  2021   Fall          2             91         8029   
5730090  November  2021   Fall          2             91         8029   
5730091  November  2021   Fall          2             91         8029   

         sales_surface_sqmeters CATEGORY         SEGMENT         MANUFACTURER  \
0                          1500     BEER           EXTRA       MANUFACTURER 2   
1                          1500     BEER           EXTRA       MANUFACTURER 2   
2                          1500     BEER           EXTRA       MANUFACTURER 2   
3                          1500     BEER           EXTRA       MANUFA

In [ ]:
_df_ventas_projected

In [47]:
### https://pypi.org/project/holidays-es/
#### https://github.com/rsolanodev/holidays-es

!pip install holidays-es

from holidays_es import Province

def obtain_holidays(provinces_df):
    for y in range(2019,2024,1):
        year_col_name = f'Holidays_{y}'
        provinces_df[year_col_name] = 0
        for i in range(len(provinces_df)):
            province = provinces_df['Provincia'][i]
            province = province.lower()
            province = province.replace(' ', '-').replace('ñ', 'n').replace('k', 'c')
            if(province == 'santa-cruz-de-tenerife' or province == 'area-metropolitana-de-barcelona' or province == 'area-metropolitana-de-madrid' ):
                province = province.split('-')[-1]
            print(province)
            holidays = Province(name=province.lower(), year=y).holidays()
            print(holidays)
            provinces_df[year_col_name][i] = holidays
    return provinces_df

#### provinces_Lat_Lon from the last fuction used to obtain the lat and lon of the provinces obtain_holidays(provinces_Lat_Lon)

In [27]:
def obtain_x_y_coords(provinces_df):
    provinces_df['Lat'] = 0
    provinces_df['Lon'] = 0
    for i in range(len(provinces_df)):
        g=geocoder.arcgis(provinces_df['Provincia'][i]+',Spain')
        provinces_df['Lat'][i] = g.latlng[0]
        provinces_df['Lon'][i] = g.latlng[1]
    return provinces_df

def obtain_holidays(provinces_df):
    for y in range(2019,2024,1):
        year_col_name = f'Holidays_{y}'
        provinces_df[year_col_name] = 0
        for i in range(len(provinces_df)):
            province = provinces_df['Provincia'][i]
            province = province.lower()
            province = province.replace(' ', '-').replace('ñ', 'n').replace('k', 'c')
            if(province == 'santa-cruz-de-tenerife' or province == 'area-metropolitana-de-barcelona' or province == 'area-metropolitana-de-madrid' ):
                province = province.split('-')[-1]
            #print(province)
            holidays = Province(name=province.lower(), year=y).holidays()
            provinces_df[year_col_name][i] = holidays
    return provinces_df

In [29]:
_df_Provinces_enriched_x_y = obtain_x_y_coords(_df_Provinces)
_df_Provinces_enriched_x_y

cod_provincia                        Provincia    Comunidad autónoma  \
0               1                            Alava            País Vasco   
1               2                         Albacete    Castilla-La Mancha   
2               3                         Alicante  Comunidad Valenciana   
3               4                          Almeria             Andalucía   
4               5                            Avila       Castilla y León   
5               6                          Badajoz           Extremadura   
6               7                         Baleares              Baleares   
7               8                        Barcelona              Cataluña   
8               9                           Burgos       Castilla y León   
9              10                          Caceres           Extremadura   
10             11                            Cadiz             Andalucía   
11             12                        Castellon  Comunidad Valenciana   
12             13                      Ciudad Real    Castilla-La Mancha   
13             14                          Cordoba             Andalucía   
14             15                        La Coruña               Galicia   
15             16                           Cuenca    Castilla-La Mancha   
16             17                           Girona              Cataluña   
17             18                          Granada             Andalucía   
18             19                      Guadalajara    Castilla-La Mancha   
19             20                        Guipuzkoa            País Vasco   
20             21                           Huelva             Andalucía   
21             22                           Huesca                Aragón   
22             23                             Jaen             Andalucía   
23             24                             Leon       Castilla y León   
24             25                           Lleida              Cataluña   
25             26                         La Rioja              La Rioja   
26             27                             Lugo               Galicia   
27             28                           Madrid                Madrid   
28             29                           Malaga             Andalucía   
29             30                           Murcia                Murcia   
30             31                          Navarra               Navarra   
31             32                          Ourense               Galicia   
32             33                         Asturias              Asturias   
33             34                         Palencia       Castilla y León   
34             35                       Las Palmas        Islas Canarias   
35             36                       Pontevedra               Galicia   
36             37                        Salamanca       Castilla y León   
37             38           Santa Cruz de Tenerife        Islas Canarias   
38             39                        Cantabria             Cantabria   
39             40                          Segovia       Castilla y León   
40             41                          Sevilla             Andalucía   
41             42                            Soria       Castilla y León   
42             43                        Tarragona              Cataluña   
43             44                           Teruel                Aragón   
44             45                           Toledo    Castilla-La Mancha   
45             46                         Valencia  Comunidad Valenciana   
46             47                       Valladolid       Castilla y León   
47             48                          Vizcaya            País Vasco   
48             49                           Zamora       Castilla y León   
49             50                         Zaragoza                Aragón   
50             91  Area Metropolitana de Barcelona              Cataluña   
51             95     Area Metropolitana de Madrid  

In [50]:
#_df_Provinces_enriched_x_y__hols_v2=obtain_holidays(_df_Provinces_enriched_x_y)
test=obtain_holidays(_df_Provinces)
#_df_Provinces_enriched_x_y__hols_v2
test

alava
{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019, 4, 19), datetime.date(2019, 5, 1), datetime.date(2019, 8, 15), datetime.date(2019, 10, 12), datetime.date(2019, 11, 1), datetime.date(2019, 12, 6), datetime.date(2019, 12, 25)], 'regional_holidays': [datetime.date(2019, 3, 19), datetime.date(2019, 4, 18), datetime.date(2019, 4, 22), datetime.date(2019, 7, 25)], 'local_holidays': [datetime.date(2019, 4, 29), datetime.date(2019, 8, 5)]}
albacete
{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019, 4, 19), datetime.date(2019, 5, 1), datetime.date(2019, 8, 15), datetime.date(2019, 10, 12), datetime.date(2019, 11, 1), datetime.date(2019, 12, 6), datetime.date(2019, 12, 25)], 'regional_holidays': [datetime.date(2019, 4, 18), datetime.date(2019, 4, 22), datetime.date(2019, 5, 31), datetime.date(2019, 6, 20)], 'local_holidays': [datetime.date(2019, 6, 24), datetime.date(2019, 9, 9)]}
alicante
{'national_holidays': [datetime.date(2019, 1, 1), datetime.d

{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019, 4, 19), datetime.date(2019, 5, 1), datetime.date(2019, 8, 15), datetime.date(2019, 10, 12), datetime.date(2019, 11, 1), datetime.date(2019, 12, 6), datetime.date(2019, 12, 25)], 'regional_holidays': [datetime.date(2019, 4, 18), datetime.date(2019, 4, 22), datetime.date(2019, 5, 31), datetime.date(2019, 6, 20)], 'local_holidays': [datetime.date(2019, 9, 12), datetime.date(2019, 9, 13)]}
guipuzcoa
{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019, 4, 19), datetime.date(2019, 5, 1), datetime.date(2019, 8, 15), datetime.date(2019, 10, 12), datetime.date(2019, 11, 1), datetime.date(2019, 12, 6), datetime.date(2019, 12, 25)], 'regional_holidays': [datetime.date(2019, 3, 19), datetime.date(2019, 4, 18), datetime.date(2019, 4, 22), datetime.date(2019, 7, 25)], 'local_holidays': [datetime.date(2019, 1, 21), datetime.date(2019, 7, 31)]}
huelva
{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2

{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019, 4, 19), datetime.date(2019, 5, 1), datetime.date(2019, 8, 15), datetime.date(2019, 10, 12), datetime.date(2019, 11, 1), datetime.date(2019, 12, 6), datetime.date(2019, 12, 25)], 'regional_holidays': [datetime.date(2019, 1, 7), datetime.date(2019, 4, 18), datetime.date(2019, 4, 23), datetime.date(2019, 12, 9)], 'local_holidays': [datetime.date(2019, 6, 12), datetime.date(2019, 9, 9)]}
tenerife
{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019, 4, 19), datetime.date(2019, 5, 1), datetime.date(2019, 8, 15), datetime.date(2019, 10, 12), datetime.date(2019, 11, 1), datetime.date(2019, 12, 6), datetime.date(2019, 12, 25)], 'regional_holidays': [datetime.date(2019, 1, 7), datetime.date(2019, 4, 18), datetime.date(2019, 5, 30)], 'local_holidays': [datetime.date(2019, 2, 2), datetime.date(2019, 3, 5), datetime.date(2019, 5, 3)]}
cantabria
{'national_holidays': [datetime.date(2019, 1, 1), datetime.date(2019,

{'national_holidays': [datetime.date(2020, 1, 1), datetime.date(2020, 1, 6), datetime.date(2020, 4, 10), datetime.date(2020, 5, 1), datetime.date(2020, 8, 15), datetime.date(2020, 10, 12), datetime.date(2020, 12, 8), datetime.date(2020, 12, 25)], 'regional_holidays': [datetime.date(2020, 3, 19), datetime.date(2020, 4, 13), datetime.date(2020, 6, 24), datetime.date(2020, 10, 9)], 'local_holidays': [datetime.date(2020, 4, 23), datetime.date(2020, 6, 22)]}
almeria
{'national_holidays': [datetime.date(2020, 1, 1), datetime.date(2020, 1, 6), datetime.date(2020, 4, 10), datetime.date(2020, 5, 1), datetime.date(2020, 8, 15), datetime.date(2020, 10, 12), datetime.date(2020, 12, 8), datetime.date(2020, 12, 25)], 'regional_holidays': [datetime.date(2020, 2, 28), datetime.date(2020, 4, 9), datetime.date(2020, 11, 2), datetime.date(2020, 12, 7)], 'local_holidays': [datetime.date(2020, 6, 24), datetime.date(2020, 8, 29)]}
avila
{'national_holidays': [datetime.date(2020, 1, 1), datetime.date(2020, 1

{'national_holidays': [datetime.date(2020, 1, 1), datetime.date(2020, 1, 6), datetime.date(2020, 4, 10), datetime.date(2020, 5, 1), datetime.date(2020, 8, 15), datetime.date(2020, 10, 12), datetime.date(2020, 12, 8), datetime.date(2020, 12, 25)], 'regional_holidays': [datetime.date(2020, 2, 28), datetime.date(2020, 4, 9), datetime.date(2020, 11, 2), datetime.date(2020, 12, 7)], 'local_holidays': [datetime.date(2020, 8, 3), datetime.date(2020, 9, 8)]}
huesca
{'national_holidays': [datetime.date(2020, 1, 1), datetime.date(2020, 1, 6), datetime.date(2020, 4, 10), datetime.date(2020, 5, 1), datetime.date(2020, 8, 15), datetime.date(2020, 10, 12), datetime.date(2020, 12, 8), datetime.date(2020, 12, 25)], 'regional_holidays': [datetime.date(2020, 4, 9), datetime.date(2020, 4, 23), datetime.date(2020, 11, 2), datetime.date(2020, 12, 7)], 'local_holidays': [datetime.date(2020, 1, 22), datetime.date(2020, 8, 10)]}
jaen
{'national_holidays': [datetime.date(2020, 1, 1), datetime.date(2020, 1, 6),

...

{'national_holidays': [datetime.date(2022, 1, 1), datetime.date(2022, 1, 6), datetime.date(2022, 4, 15), datetime.date(2022, 8, 15), datetime.date(2022, 10, 12), datetime.date(2022, 11, 1), datetime.date(2022, 12, 6), datetime.date(2022, 12, 8)], 'regional_holidays': [datetime.date(2022, 4, 14), datetime.date(2022, 4, 23), datetime.date(2022, 5, 2), datetime.date(2022, 12, 26)], 'local_holidays': [datetime.date(2022, 4, 19), datetime.date(2022, 7, 11)]}
toledo
{'national_holidays': [datetime.date(2022, 1, 1), datetime.date(2022, 1, 6), datetime.date(2022, 4, 15), datetime.date(2022, 8, 15), datetime.date(2022, 10, 12), datetime.date(2022, 11, 1), datetime.date(2022, 12, 6), datetime.date(2022, 12, 8)], 'regional_holidays': [datetime.date(2022, 4, 14), datetime.date(2022, 5, 31), datetime.date(2022, 6, 16), datetime.date(2022, 12, 26)], 'local_holidays': [datetime.date(2022, 3, 19), datetime.date(2022, 4, 18)]}
valencia
{'national_holidays': [datetime.date(2022, 1, 1), datetime.date(202

{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7), datetime.date(2023, 5, 1), datetime.date(2023, 8, 15), datetime.date(2023, 10, 12), datetime.date(2023, 11, 1), datetime.date(2023, 12, 6), datetime.date(2023, 12, 8), datetime.date(2023, 12, 25)], 'regional_holidays': [datetime.date(2023, 2, 21), datetime.date(2023, 4, 6), datetime.date(2023, 9, 8)], 'local_holidays': [datetime.date(2023, 4, 24), datetime.date(2023, 5, 26)]}
cadiz
{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7), datetime.date(2023, 5, 1), datetime.date(2023, 8, 15), datetime.date(2023, 10, 12), datetime.date(2023, 11, 1), datetime.date(2023, 12, 6), datetime.date(2023, 12, 8), datetime.date(2023, 12, 25)], 'regional_holidays': [datetime.date(2023, 1, 2), datetime.date(2023, 2, 28), datetime.date(2023, 4, 6)], 'local_holidays': [datetime.date(2023, 2, 20), datetime.date(2023, 10, 7)]}
castellon
{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4,

{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7), datetime.date(2023, 5, 1), datetime.date(2023, 8, 15), datetime.date(2023, 10, 12), datetime.date(2023, 11, 1), datetime.date(2023, 12, 6), datetime.date(2023, 12, 8), datetime.date(2023, 12, 25)], 'regional_holidays': [datetime.date(2023, 3, 20), datetime.date(2023, 4, 6), datetime.date(2023, 5, 2)], 'local_holidays': [datetime.date(2023, 5, 15), datetime.date(2023, 11, 9)]}
malaga
{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7), datetime.date(2023, 5, 1), datetime.date(2023, 8, 15), datetime.date(2023, 10, 12), datetime.date(2023, 11, 1), datetime.date(2023, 12, 6), datetime.date(2023, 12, 8), datetime.date(2023, 12, 25)], 'regional_holidays': [datetime.date(2023, 1, 2), datetime.date(2023, 2, 28), datetime.date(2023, 4, 6)], 'local_holidays': [datetime.date(2023, 8, 19), datetime.date(2023, 9, 8)]}
murcia
{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7)

{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7), datetime.date(2023, 5, 1), datetime.date(2023, 8, 15), datetime.date(2023, 10, 12), datetime.date(2023, 11, 1), datetime.date(2023, 12, 6), datetime.date(2023, 12, 8), datetime.date(2023, 12, 25)], 'regional_holidays': [datetime.date(2023, 4, 10), datetime.date(2023, 6, 24), datetime.date(2023, 10, 9)], 'local_holidays': [datetime.date(2023, 4, 17), datetime.date(2023, 4, 24)]}
valladolid
{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023, 4, 7), datetime.date(2023, 5, 1), datetime.date(2023, 8, 15), datetime.date(2023, 10, 12), datetime.date(2023, 11, 1), datetime.date(2023, 12, 6), datetime.date(2023, 12, 8), datetime.date(2023, 12, 25)], 'regional_holidays': [datetime.date(2023, 1, 2), datetime.date(2023, 4, 6), datetime.date(2023, 7, 25)], 'local_holidays': [datetime.date(2023, 5, 13), datetime.date(2023, 9, 8)]}
vizcaya
{'national_holidays': [datetime.date(2023, 1, 6), datetime.date(2023

cod_provincia                        Provincia    Comunidad autónoma  \
0               1                            Alava            País Vasco   
1               2                         Albacete    Castilla-La Mancha   
2               3                         Alicante  Comunidad Valenciana   
3               4                          Almeria             Andalucía   
4               5                            Avila       Castilla y León   
5               6                          Badajoz           Extremadura   
6               7                         Baleares              Baleares   
7               8                        Barcelona              Cataluña   
8               9                           Burgos       Castilla y León   
9              10                          Caceres           Extremadura   
10             11                            Cadiz             Andalucía   
11             12                        Castellon  Comunidad Valenciana   
12             13                      Ciudad Real    Castilla-La Mancha   
13             14                          Cordoba             Andalucía   
14             15                        La Coruña               Galicia   
15             16                           Cuenca    Castilla-La Mancha   
16             17                           Girona              Cataluña   
17             18                          Granada             Andalucía   
18             19                      Guadalajara    Castilla-La Mancha   
19             20                        Guipuzkoa            País Vasco   
20             21                           Huelva             Andalucía   
21             22                           Huesca                Aragón   
22             23                             Jaen             Andalucía   
23             24                             Leon       Castilla y León   
24             25                           Lleida              Cataluña   
25             26                         La Rioja              La Rioja   
26             27                             Lugo               Galicia   
27             28                           Madrid                Madrid   
28             29                           Malaga             Andalucía   
29             30                           Murcia                Murcia   
30             31                          Navarra               Navarra   
31             32                          Ourense               Galicia   
32             33                         Asturias              Asturias   
33             34                         Palencia       Castilla y León   
34             35                       Las Palmas        Islas Canarias   
35             36                       Pontevedra               Galicia   
36             37                        Salamanca       Castilla y León   
37             38           Santa Cruz de Tenerife        Islas Canarias   
38             39                        Cantabria             Cantabria   
39             40                          Segovia       Castilla y León   
40             41                          Sevilla             Andalucía   
41             42                            Soria       Castilla y León   
42             43                        Tarragona              Cataluña   
43             44                           Teruel                Aragón   
44             45                           Toledo    Castilla-La Mancha   
45             46                         Valencia  Comunidad Valenciana   
46             47                       Valladolid       Castilla y León   
47             48                          Vizcaya            País Vasco   
48             49                           Zamora       Castilla y León   
49             50                         Zaragoza                Aragón   
50             91  Area Metropolitana de Barcelona              Cataluña   
51             95     Area Metropolitana de Madrid  

In [ ]:
# group by region and product, and sum sales
grouped_data = _df_ventas_historic.groupby(['Comunidad autónoma', 'Provincia', 'SEGMENT']).sum().reset_index()
grouped_data

In [ ]:
# get top 5 product sales per province per municipality
top_5_data = grouped_data.groupby(['Comunidad autónoma', 'Provincia']).apply(lambda x: x.nlargest(5, 'ventas_valor')).reset_index(drop=True)
top_5_data

In [ ]:
test=top_5_data.merge(_df_Provinces, on='Provincia', how='left')
test


In [ ]:
# read in province boundaries from GeoJSON file
with open('gadm41_ESP_4.json') as f:
    province_geojson = json.load(f)

# create map
map = folium.Map(location=[40.4168, -3.7038], zoom_start=6)


# add province boundaries to map
folium.GeoJson(province_geojson, name='geojson').add_to(map)

# add markers for top 10 product sales per region
for index, row in test.iterrows():
    comunidad = row['Comunidad autónoma_x']
    #print(comunidad)
    province = row['Provincia']
    #print(province)
    product = row['SEGMENT']
   # print(product)
    sales = row['ventas_valor']
    #print(sales)
    latitude = row['Lat']
    longitude = row['Lon']
    # get province boundary from GeoJSON file
    province_boundary = next((feature for feature in province_geojson['features'] if feature['properties']['NAME_1'] == province), None)
    print(province_boundary)
    if province_boundary:
        # add marker to province centroid
        centroid = folium.GeoJson(province_boundary).get_bounds()[::-1]
        # add random noise to centroid to spread out markers
        noise = np.random.normal(scale=0.01, size=2)
        noisy_centroid = centroid + noise
        folium.Marker(location=(latitude, longitude), tooltip=f'{province}: {product}: {sales}').add_to(map)

# display map

map

In [ ]:
# read in province boundaries from GeoJSON file
with open('gadm41_ESP_4.json') as f:
    province_geojson = json.load(f)

# create map
map = folium.Map(location=[40.4168, -3.7038], zoom_start=6)


# add province boundaries to map
#folium.GeoJson(province_geojson, name='geojson').add_to(map)

# add markers for top 10 product sales per region
for index, row in test.iterrows():
    comunidad = row['Comunidad autónoma_x']
    #print(comunidad)
    province = row['Provincia']
    #print(province)
    product = row['SEGMENT']
   # print(product)
    sales = row['ventas_valor']
    #print(sales)
    latitude = row['Lat']
    longitude = row['Lon']
    folium.Marker(location=(latitude, longitude), tooltip=f'{province}: {product}: {sales}').add_to(map)

# display map

map

In [ ]:
provinces = {}
for feature in province_geojson['features']:
    properties = feature['properties']
    province_name = properties['NAME_2']
    geometry = feature['geometry']
    if geometry['type'] == 'MultiPolygon':
        coordinates = geometry['coordinates'][0][0][0]
    elif geometry['type'] == 'Polygon':
        coordinates = geometry['coordinates'][0]
    provinces[province_name] = coordinates

In [ ]:
communidad = {}
for feature in province_geojson['features']:
    properties = feature['properties']
    province_name = properties['NAME_4']
    geometry = feature['geometry']
    if geometry['type'] == 'MultiPolygon':
        coordinates = geometry['coordinates'][0][0][0]
    elif geometry['type'] == 'Polygon':
        coordinates = geometry['coordinates'][0]
    communidad[province_name] = coordinates
communidad